# Scientific Article Literature Clustering by NLP

Oscar Charles 2021

Question: Can we use Natural Language processing to take a set of abstracts (strings) -> tokens -> vectorisation -> clustering of abstracts by similarity?
We have a set of papers we want to cluster close together, can we get them too such that we can find similar papers we may have missed?

Uses: Pubmed , you will need Eztrez Direct to use this scripts pubmed api calls https://www.ncbi.nlm.nih.gov/books/NBK179288/

## First Get some Data


In [163]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import xml.etree.ElementTree as ET
#! python -m spacy download en_core_web_sm
#! pip install bokeh

In [164]:
# pubmed has all papers, epmc only those that are openly accessible.

# current
"((resistance)) AND ((mutation)) AND ((ribavirin) OR (favipiravir) OR (remdesivir) OR (EIDD-2801) OR (molnupiravir)) " 
# quick
"rna AND virus AND drug AND resistance AND MUTATION"
# Conduct a PubMed search and retrieve the results as a list of PMIDs
! /home/oc/edirect/esearch -db pubmed -query " antiviral AND resistance AND mutation " | /home/oc/edirect/efetch -format uid > pubmed.txt

# how many entries?
! wc -l pubmed.txt 

# take those identified pubmed ids of interest and 
! /home/oc/edirect/efetch -db pubmed -input pubmed.txt -format xml > pubmed.xml

# sanity check
#! head -5 pubmed.xml

4421 pubmed.txt


In [165]:
# parse xml
dict_ = {'doi': [], 'title': [], 'abstract':[]}

tree = ET.parse('pubmed.xml') # download from a search in epmc
root = tree.getroot()

search_doi = 'MedlineCitation/Article/ELocationID'
search_title = 'MedlineCitation/Article/ArticleTitle'
search_abstract = 'MedlineCitation/Article/Abstract/AbstractText'

for entry in root.iter('PubmedArticle'):
    if entry.find(search_doi) is None:
        continue
    else:
        doi = entry.find(search_doi).text
        
    if entry.find(search_title) is None:
        continue
    else:
        title = entry.find(search_title).text
        
    if entry.find(search_abstract) is None:
        continue
    else:
        abstractText = entry.find(search_abstract).text
    #print(doi, title)
    dict_['doi'].append(doi)
    dict_['title'].append(title)
    dict_['abstract'].append(abstractText)


In [166]:
# format the dict to a table
df = pd.DataFrame(dict_, columns=['doi', 'title','abstract'])
df.head()

doi  \
0  10.1007/s00894-021-05005-7   
1                         156   
2                        2535   
3   10.3389/fmicb.2021.774711   
4    10.18502/ijph.v50i8.6804   

                                               title  \
0  The effects of mutation on the drug binding af...   
1  Altered HIV-1 mRNA Splicing Due to Drug-Resist...   
2  Influence of Ribavirin on Mumps Virus Populati...   
3  Viral Evasion of Innate Immune Defense: The Ca...   
4  Evaluation of the Outcome of Antiviral Therapy...   

                                            abstract  
0  The influenza virus is an important respirator...  
1  The underlying molecular mechanism and their g...  
2  Frequent mumps outbreaks in vaccinated populat...  
3  Mannose-binding lectins effectively inhibit mo...  
4  To evaluate the condition of antiviral therapy...

In [167]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2646 entries, 0 to 2645
Data columns (total 3 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   doi       2646 non-null   object
 1   title     2646 non-null   object
 2   abstract  2646 non-null   object
dtypes: object(3)
memory usage: 62.1+ KB


In [168]:
len(df)

2646

## Parse

In [169]:
#NLP 
import spacy
from spacy.lang.en.stop_words import STOP_WORDS
from spacy.lang.en import English

# using scispacy we can add support for scientific abbreviations
from scispacy.abbreviation import AbbreviationDetector

parser = spacy.load("en_core_sci_sm") # scispacy model
# Add the abbreviation pipe to the spacy pipeline.
parser.add_pipe("abbreviation_detector")


In [170]:
import string

punctuations = string.punctuation
stopwords = list(STOP_WORDS)
stopwords[:10]

['and',
 'enough',
 'however',
 'although',
 'my',
 'along',
 'please',
 'least',
 'did',
 'after']

In [171]:
# stop words are words that are removed, we want to append the virus as thats providing most clustering signal.
custom_stop_words = [
    'doi', 'preprint', 'copyright', 'peer', 'reviewed', 'org', 'https', 'et', 'al', 'author', 'figure', 
    'rights', 'reserved', 'permission', 'used', 'using', 'biorxiv', 'medrxiv', 'license', 'fig', 'fig.', 
    'al.', 'Elsevier', 'PMC', 'CZI', 'www',
    "Hepatitis C", "Herpes", "Simplex 1", "Simplex 2", "Cytomegalovirus", "Coronavirus", "HCMV", "CMV", "HSV1", "HSV2", 
    "influenza A", "(H1N1)", "HIV-1", "HIV", "Hepatitis B", "HCV", "HBV",
    "SARS-COV-2", "COVID-19", "COVID", "human immunodeficiency virus", "HIV-RNA", "subtype", "genotype", "subtype",
    "avian influenza", "syncytial", "polio", "poliovirus", "chikungunya"
    
]

for w in custom_stop_words:
    if w not in stopwords:
        stopwords.append(w)

In [172]:
# Parser

parser.max_length = 7000000

def call_tokenizer(df):
    df["processed_abstract"] = df["abstract"].apply(spacy_tokenizer)
    return df

def spacy_tokenizer(sentence):
    mytokens = parser(sentence)
    mytokens = [ word.lemma_.lower().strip() if word.lemma_ != "-PRON-" else word.lower_ for word in mytokens ]
    mytokens = [ word for word in mytokens if word not in stopwords and word not in punctuations ]
    mytokens = " ".join([i for i in mytokens])
    return mytokens

In [173]:
from multiprocessing import  Pool

def parallelize_dataframe(df, func, n_cores=4):
    df_split = np.array_split(df, n_cores)
    pool = Pool(n_cores)
    df = pd.concat(pool.map(func, df_split))
    pool.close()
    pool.join()
    return df

In [174]:
%%capture --no-stdout
# scispacy abbreviation complains each time a abstract has no abbreviations it knows.... stop that warning.
# tokenise
# single core
#df["processed_abstract"] = df["abstract"].apply(spacy_tokenizer)
%time df = parallelize_dataframe(df=df, func=call_tokenizer, n_cores=32)

CPU times: user 49.3 ms, sys: 770 ms, total: 819 ms
Wall time: 4.13 s


### Save

In [175]:
import pickle
pickle.dump(df, open("tokenised_df.p", "wb" ))

## Vectorize

In [176]:
df = pickle.load(open("tokenised_df.p", "rb"))
#df = df.sample(600000)

In [177]:
from sklearn.feature_extraction.text import TfidfVectorizer
def vectorize(text, maxx_features):
    
    vectorizer = TfidfVectorizer(max_features=maxx_features)
    X = vectorizer.fit_transform(text)
    return X

In [178]:
text = df['processed_abstract'].values
%time X = vectorize(text, 2 ** 12)
X.shape

CPU times: user 132 ms, sys: 12 ms, total: 144 ms
Wall time: 144 ms


(2646, 4096)

## Cluster

In [179]:
from sklearn.cluster import KMeans

In [180]:
k = 20
kmeans = KMeans(n_clusters=k, random_state=42)
%time y_pred = kmeans.fit_predict(X)
df['y'] = y_pred

CPU times: user 14 s, sys: 0 ns, total: 14 s
Wall time: 1.3 s


## Libraries for Plotting

In [181]:
%matplotlib inline
from matplotlib import pyplot as plt
import seaborn as sns

## TSNE GPU

First reduce noise using PCA by extracting the first 20 principle components:

In [182]:
from sklearn.decomposition import PCA

pca = PCA(n_components=30, random_state=42)
%time X_embedded_pca= pca.fit_transform(X.toarray())
X_embedded_pca.shape

CPU times: user 13.8 s, sys: 25.1 s, total: 38.9 s
Wall time: 685 ms


(2646, 20)

In [183]:
from sklearn.manifold import TSNE
X_embedded_tsne = TSNE(n_components=2, learning_rate='auto',init='random').fit_transform(X_embedded_pca)
df['x_tsne'] = X_embedded_tsne[:,0] 
df['y_tsne'] = X_embedded_tsne[:,1]

#from tsnecuda import TSNE
#%time X_embedded_tsne = TSNE(n_components=2, learning_rate=30, n_iter=500000, verbose=1).fit_transform(X_embedded_pca)

In [184]:
# we want bokeh to treat y (cluster) as discrete not continuous 
df['y'] = df['y'].apply(str)
df.dtypes

doi                    object
title                  object
abstract               object
processed_abstract     object
y                      object
x_tsne                float32
y_tsne                float32
dtype: object

In [185]:
# identify which papers we know are of interest, then make them squares. maybe we need to hide the virus name from the model?
key_doi=["10.1371/journal.ppat.1009929",
"10.1128/mBio.00221-18",
"10.1128/JVI.01965-17",
"10.1073/pnas.1811345115",
"10.1093/jac/dku209",
"10.1128/AAC.01073-16",
"10.1073/pnas.1232294100",
"10.1128/JVI.02139-12",
"10.1016/j.antiviral.2013.07.008",
"10.1371/journal.ppat.1001163",
"10.1128/JVI.00289-14",
"10.1073/pnas.1111650108",
"10.1128/JVI.79.4.2346-2355.2005",
"10.1128/JVI.03594-13",
"10.1128/JVI.01297-08",
"10.1371/journal.ppat.1003877"]
df['key'] = df['doi'].isin(key_doi)
df[df['doi'].isin(key_doi)]

doi  \
35       10.1371/journal.ppat.1009929   
490           10.1073/pnas.1811345115   
894              10.1128/AAC.01073-16   
1299               10.1093/jac/dku209   
1375             10.1128/JVI.00289-14   
1407             10.1128/JVI.03594-13   
1522  10.1016/j.antiviral.2013.07.008   
1686             10.1128/JVI.02139-12   
2127     10.1371/journal.ppat.1001163   

                                                  title  \
35    In vitro selection of Remdesivir resistance su...   
490   The mechanism of resistance to favipiravir in ...   
894   In Vitro Assessment of Combinations of Enterov...   
1299  Mutations in the chikungunya virus non-structu...   
1375  Attenuation of human enterovirus 71 high-repli...   
1407  Ribavirin-resistant variants of foot-and-mouth...   
1522  An increased replication fidelity mutant of fo...   
1686  Ribavirin-resistant mutants of human enterovir...   
2127  Fidelity variants of RNA dependent RNA polymer...   

                                               abstract  \
35    Remdesivir (RDV), a broadly acting nucleoside ...   
490   Favipiravir is a broad-spectrum antiviral that...   
894   Enterovirus 71 (EV-A71) is a major causative p...   
1299  T-705, also known as favipiravir, is a small-m...   
1375  In a screen for ribavirin resistance, a novel ...   
1407  Mutagenic nucleoside analogues can be used to ...   
1522  In a screen for RNA mutagen-resistant foot-and...   
1686  It has been shown in animal models that ribavi...   
2127  In a screen for RNA mutagen resistance, we iso...   

                                     processed_abstract   y     x_tsne  \
35    remdesivir rdv broadly act nucleoside analogue...  14  20.326475   
490   favipiravir broad-spectrum antiviral promise t...  14  29.084614   
894   enterovirus 71 ev-a71 major causative pathogen...   6   8.295137   
1299  t-705 know favipiravir small-molecule inhibito...  14  12.664795   
1375  screen ribavirin resistance novel high-fidelit...  14  27.110842   
1407  mutagenic nucleoside analogue use isolate rna ...  14  28.098989   
1522  screen rna mutagen-resistant foot-and-mouth di...  14  28.213049   
1686  animal model ribavirin-resistant g64s mutation...  14  25.305695   
2127  screen rna mutagen resistance isolate high fid...  14  27.862682   

        y_tsne   key  
35    3.100855  True  
490   5.562101  True  
894   5.621903  True  
1299  2.077208  True  
1375  7.590344  True  
1407  8.584375  True  
1522  8.857230  True  
1686  6.296982  True  
2127  8.262935  True

In [186]:
# make a pretty plot
from bokeh.plotting import ColumnDataSource, figure, output_notebook, show, output_file, save
from bokeh.palettes import d3
import bokeh.models as bmo
#output_file("toolbar.html")
output_notebook()

TOOLTIPS = [
    ("index", "$index"),
    ("(x,y)", "($x, $y)"),
    ("doi", "@doi"),
    ("title", "@title"),
]

# use whatever palette you want...
palette = d3['Category20'][len(df['y'].unique())]
color_map = bmo.CategoricalColorMapper(factors=df['y'].unique(),
                                   palette=palette)

p = figure(width=800, height=800, tooltips=TOOLTIPS,
           title="Mouse over the dots")
p.scatter('x_tsne', 'y_tsne', size=5, source=df[df['key'] == False], color={'field': 'y', 'transform': color_map})
p.scatter('x_tsne', 'y_tsne', size=8, source=df[df['key'] == True], color="black", marker="square")
show(p)


Loading BokehJS ...

In [187]:
# when tooltip is hovering over a inteeresting article, search for bits of its doi
df[df['doi'].str.contains("78-16")]

doi                                              title  \
819             e01878-16  ϕX174 Procapsid Assembly: Effects of an Inhibi...   
881  10.1128/JVI.00078-16  Poliovirus Polymerase Leu420 Facilitates RNA R...   

                                              abstract  \
819  During ϕX174 morphogenesis, 240 copies of the ...   
881  RNA recombination is important in the formatio...   

                                    processed_abstract   y     x_tsne  \
819  ϕx174 morphogenesis 240 copy external scaffold...   6   0.713605   
881  rna recombination important formation picornav...  14  24.820589   

       y_tsne    key  
819 -5.877970  False  
881  8.723691  False

In [188]:
# references
#https://github.com/MaksimEkin/arXiv-Literature-Clustering

In [189]:
! pip freeze > req.txt